In [1]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

In [91]:
class Sphere:
    
    #init method
    def __init__(self, num_lat,num_lon,temp_type):
        self.num_lat=num_lat
        self.num_lon=num_lon
        self.temp_type=temp_type
        
    def make_lat(self):
        #creates an array of latitudes (phi)
        phi=np.linspace(0,np.pi,self.num_lat)
        self.phi=phi
        return phi
        
    def make_lon(self):
        #creates an array of longitudes (theta)
        theta=np.linspace(0,2*np.pi,self.num_lon)
        self.theta=theta
        return theta
        
    def make_temp(self,custom_data="None",mean_temp=1000):
        #creates the temperature field
        
        if self.temp_type=="uniform":
            #creates uniform temperature field
            data=mean_temp*np.ones((self.num_lat,self.num_lon))

        elif self.temp_type=="zonal":
            #creates zonal temperature field
            lat=self.make_lat()
            data=np.sin(lat)*mean_temp*np.ones((self.num_lon,self.num_lat))  
        
        elif self.temp_type=="custom":
            #uses an array
            data=custom_data
        print(np.shape(data))
        self.temp=data
        return data

    def get_temp(self):
        
        temp=self.temp
        return temp

In [105]:

    
def make_hoverdata(x,y,z,input_temp):
    """
    Makes the data that appear when hovering over a point on a sphere,
    namely latitude, longitude, and the temperature value

    Parameters
    ----------
    x : array
        array of x coordinates for the sphere.
    y : array
        array of y coordinates for the sphere.
    z : array
        array of z coordinates for the sphere.
    input_temp : array
        temperature field

    Returns
    -------
    hoverdata : array
        Stack of latitude, longitude, and temperature field arrays

    """
    
    trunc_temp= input_temp.round(decimals=0)
    
    lats=np.arcsin(z)*180/np.pi
    lats=lats.round(decimals=1)
    
    lons=2*np.arctan(np.divide(y,(x**2+y**2)))*180/np.pi
    lons=lons.round(decimals=1)
    
    print(np.shape(lats))
    print(np.shape(lons))
    print(np.shape(trunc_temp))
    
    hoverdata=np.stack((lats.T, lons.T, trunc_temp.T), axis =-1)
    
    return hoverdata


In [106]:
def plot_sphere(planet,theta,phi,temp,save=False,name="None"):
    """
    This function creates the interacti
    """
    x = np.outer(np.cos(theta),np.sin(phi))
    y = np.outer(np.sin(theta),np.sin(phi))
    z = np.outer(np.ones(129),np.cos(phi))

    x = np.outer(np.cos(theta),np.sin(phi))
    y = np.outer(np.sin(theta),np.sin(phi))
    z = np.outer(np.ones(planet.num_lon),np.cos(phi))
    
    
    hoverdata=make_hoverdata(x,y,z,temp)
    #call plotly
    fig= go.Figure(go.Surface(x=x, y=y, z=z,surfacecolor=temp,cmax=1200,cmin=700,colorscale='jet',customdata=hoverdata,    hovertemplate ="lat: %{customdata[0]}"+\
                             "<br>lon: %{customdata[1]}"+\
                             "<br>temp:%{customdata[2]} K<extra></extra>"))

    
    fig.update_layout(scene = dict(
                        xaxis = dict(
                             showbackground=False,visible=False),
                        yaxis = dict(
                             showbackground=False,visible=False),
                        zaxis = dict(
                             showbackground=False,visible=False)))
                      
    fig.show()

    if save==1:
        fig.write_html(name+".html")

## Try making and plotting a sphere

In [107]:
planet=Sphere(63,129,"custom")

In [108]:
def import_csv(path):
    """
    Reads the .csv file as a pandas data frame and returns the values

    Parameters
    ----------
    path : string
        Path to the .csv data to be imported.

    Returns
    -------
    array
        numpy array of the data read

    """
    df=pd.read_csv(path)
    return df.values

def fill_in_data(temp_data):
    """
    Fills in the data gap to make sure the sphere is plotted continuously.

    Parameters
    ----------
    temp_data : array
        Temperature field data

    Returns
    -------
    input_temp : array
        Temperature filled with the gap filled in.

    """
    to_append = (temp_data[:,0] + temp_data[:,-1])*0.5
    to_append = to_append.reshape((len(to_append),1))
    temp = np.append(temp_data,to_append,axis=1).T
    return temp


In [109]:
hjvals=import_csv('./data/hot_Jupiter_snapshot.csv')
input_temp=fill_in_data(hjvals)
print(input_temp.shape)

(129, 63)


In [117]:
theta=planet.make_lon()
print(len(theta))

129


In [111]:
phi=planet.make_lat()

In [112]:
temp=planet.make_temp(custom_data=input_temp)

(129, 63)


In [113]:
plot_sphere(planet,theta,phi,temp,save=True,name='testsaveHJ')

C:\Users\ek672\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:29: RuntimeWarning:

invalid value encountered in true_divide



(129, 63)
(129, 63)
(129, 63)


In [114]:
planet2=Sphere(100,200,"zonal")

In [118]:
theta=planet2.make_lon()
phi=planet2.make_lat()
temp=(planet2.make_temp())
print(np.shape(planet2.temp))

(200, 100)
(200, 100)


In [120]:
plot_sphere(planet2,theta,phi,temp)

C:\Users\ek672\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:29: RuntimeWarning:

invalid value encountered in true_divide



(200, 100)
(200, 100)
(200, 100)
